In [1]:
import re 
import torch
import pickle 
import numpy as np
import pandas as pd
from tqdm import tqdm
from nltk.tokenize import word_tokenize
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split

In [2]:
lr = 0.0001 #learning Rate
input_size = 50
num_epochs = 100
hidden_size = 50 
label_col = 'Product'
text_col_name = "Consumer complaint narrative"
label_encoder_path = "Output/label_encoder.pkl"
product_map = {'Vehicle loan or lease': 'vehicle_loan',
               'Credit reporting, credit repair services, or other personal consumer reports': 'credit_report',
               'Credit card or prepaid card': 'card',
               'Money transfer, virtual currency, or money service': 'money_transfer',
               'virtual currency': 'money_transfer',
               'Mortgage': 'mortgage',
               'Payday loan, title loan, or personal loan': 'loan',
               'Debt collection': 'debt_collection',
               'Checking or savings account': 'savings_account',
               'Credit card': 'card',
               'Bank account or service': 'savings_account',
               'Credit reporting': 'credit_report',
               'Prepaid card': 'card',
               'Payday loan': 'loan',
               'Other financial service': 'others',
               'Virtual currency': 'money_transfer',
               'Student loan': 'loan',
               'Consumer Loan': 'loan',
               'Money transfers': 'money_transfer'}

In [3]:
# define function for saving a file
def save_file(name, obj):
    """
    Function to save an object as pickle file
    """
    with open(name, 'wb') as f:
        pickle.dump(obj, f)

# define function for loading a file
def load_file(name):
    """
    Function to load a pickle object
    """
    return pickle.load(open(name, "rb"))

In [4]:
Glove_path = "D:\Project\RNN LSTM TEXT CLASSIFICATION\Output\glove.6B.50d.txt"

## Process glove embeddings

In [5]:
with open(Glove_path,'rt',encoding='utf-8') as f:
    emb = f.readlines()

## 40000 unique words are there in the embedding

In [6]:
len(emb)

400000

## Check the first record

In [7]:
# check first record
emb[0]

'the 0.418 0.24968 -0.41242 0.1217 0.34527 -0.044457 -0.49688 -0.17862 -0.00066023 -0.6566 0.27843 -0.14767 -0.55677 0.14658 -0.0095095 0.011658 0.10204 -0.12792 -0.8443 -0.12181 -0.016801 -0.33279 -0.1552 -0.23131 -0.19181 -1.8823 -0.76746 0.099051 -0.42125 -0.19526 4.0071 -0.18594 -0.52287 -0.31681 0.00059213 0.0074449 0.17778 -0.15897 0.012041 -0.054223 -0.29871 -0.15749 -0.34758 -0.045637 -0.44251 0.18785 0.0027849 -0.18411 -0.11514 -0.78581\n'

In [8]:
# split the first record and check for vocabulary
emb[0].split()[0]

'the'

In [9]:
# split the record and check for embeddings
emb[0].split()[1:]

['0.418',
 '0.24968',
 '-0.41242',
 '0.1217',
 '0.34527',
 '-0.044457',
 '-0.49688',
 '-0.17862',
 '-0.00066023',
 '-0.6566',
 '0.27843',
 '-0.14767',
 '-0.55677',
 '0.14658',
 '-0.0095095',
 '0.011658',
 '0.10204',
 '-0.12792',
 '-0.8443',
 '-0.12181',
 '-0.016801',
 '-0.33279',
 '-0.1552',
 '-0.23131',
 '-0.19181',
 '-1.8823',
 '-0.76746',
 '0.099051',
 '-0.42125',
 '-0.19526',
 '4.0071',
 '-0.18594',
 '-0.52287',
 '-0.31681',
 '0.00059213',
 '0.0074449',
 '0.17778',
 '-0.15897',
 '0.012041',
 '-0.054223',
 '-0.29871',
 '-0.15749',
 '-0.34758',
 '-0.045637',
 '-0.44251',
 '0.18785',
 '0.0027849',
 '-0.18411',
 '-0.11514',
 '-0.78581']

## Separate embeddings and vocabulary

In [10]:
vocabulary, embeddings = [], []

for item in emb:
    vocabulary.append(item.split()[0])
    embeddings.append(item.split()[1:])

In [11]:
vocabulary

['the',
 ',',
 '.',
 'of',
 'to',
 'and',
 'in',
 'a',
 '"',
 "'s",
 'for',
 '-',
 'that',
 'on',
 'is',
 'was',
 'said',
 'with',
 'he',
 'as',
 'it',
 'by',
 'at',
 '(',
 ')',
 'from',
 'his',
 "''",
 '``',
 'an',
 'be',
 'has',
 'are',
 'have',
 'but',
 'were',
 'not',
 'this',
 'who',
 'they',
 'had',
 'i',
 'which',
 'will',
 'their',
 ':',
 'or',
 'its',
 'one',
 'after',
 'new',
 'been',
 'also',
 'we',
 'would',
 'two',
 'more',
 "'",
 'first',
 'about',
 'up',
 'when',
 'year',
 'there',
 'all',
 '--',
 'out',
 'she',
 'other',
 'people',
 "n't",
 'her',
 'percent',
 'than',
 'over',
 'into',
 'last',
 'some',
 'government',
 'time',
 '$',
 'you',
 'years',
 'if',
 'no',
 'world',
 'can',
 'three',
 'do',
 ';',
 'president',
 'only',
 'state',
 'million',
 'could',
 'us',
 'most',
 '_',
 'against',
 'u.s.',
 'so',
 'them',
 'what',
 'him',
 'united',
 'during',
 'before',
 'may',
 'since',
 'many',
 'while',
 'where',
 'states',
 'because',
 'now',
 'city',
 'made',
 'like',
 

## Convert embeddings to numpy float array

In [12]:
embeddings = np.array(embeddings,dtype = np.float32)

In [13]:
embeddings.shape

(400000, 50)

## Add embeddings for padding and unknown items

In [14]:
vocabulary[:10]

['the', ',', '.', 'of', 'to', 'and', 'in', 'a', '"', "'s"]

In [15]:
embeddings

array([[ 0.418   ,  0.24968 , -0.41242 , ..., -0.18411 , -0.11514 ,
        -0.78581 ],
       [ 0.013441,  0.23682 , -0.16899 , ..., -0.56657 ,  0.044691,
         0.30392 ],
       [ 0.15164 ,  0.30177 , -0.16763 , ..., -0.35652 ,  0.016413,
         0.10216 ],
       ...,
       [-0.51181 ,  0.058706,  1.0913  , ..., -0.25003 , -1.125   ,
         1.5863  ],
       [-0.75898 , -0.47426 ,  0.4737  , ...,  0.78954 , -0.014116,
         0.6448  ],
       [ 0.072617, -0.51393 ,  0.4728  , ..., -0.18907 , -0.59021 ,
         0.55559 ]], dtype=float32)

In [16]:
vocabulary = ["<pad>","<unk>"] + vocabulary

In [17]:
embeddings = np.vstack([np.ones(50,dtype=np.float32),np.mean(embeddings,axis=0),embeddings])

In [18]:
embeddings

array([[ 1.        ,  1.        ,  1.        , ...,  1.        ,
         1.        ,  1.        ],
       [-0.12920076, -0.28866628, -0.01224866, ...,  0.10069408,
         0.00653003,  0.01685157],
       [ 0.418     ,  0.24968   , -0.41242   , ..., -0.18411   ,
        -0.11514   , -0.78581   ],
       ...,
       [-0.51181   ,  0.058706  ,  1.0913    , ..., -0.25003   ,
        -1.125     ,  1.5863    ],
       [-0.75898   , -0.47426   ,  0.4737    , ...,  0.78954   ,
        -0.014116  ,  0.6448    ],
       [ 0.072617  , -0.51393   ,  0.4728    , ..., -0.18907   ,
        -0.59021   ,  0.55559   ]], dtype=float32)

In [19]:
print(len(vocabulary),embeddings.shape)

400002 (400002, 50)


In [20]:
vocabulary_path = r"C:\Users\Anonymous\OneDrive\RNN AND LSTM\output\vocabulary.pkl"

In [21]:
embeddings_path = r"C:\Users\Anonymous\OneDrive\RNN AND LSTM\output\embeddings.pkl"

## Save embeddings and Vocabulary

In [22]:
save_file(vocabulary_path,vocabulary)
save_file(embeddings_path,embeddings)

## Process text data

In [23]:
data = pd.read_csv("D:\Project\RNN LSTM TEXT CLASSIFICATION\Data\complaints.csv")

In [24]:
data.head()

Date received                                            Product  \
0    2019-06-13  Credit reporting, credit repair services, or o...   
1    2019-11-01                              Vehicle loan or lease   
2    2019-04-01  Credit reporting, credit repair services, or o...   
3    2021-11-01  Credit reporting, credit repair services, or o...   
4    2021-11-02                                    Debt collection   

        Sub-product                                              Issue  \
0  Credit reporting               Incorrect information on your report   
1              Loan                        Struggling to pay your loan   
2  Credit reporting               Incorrect information on your report   
3  Credit reporting  Problem with a credit reporting company's inve...   
4      Medical debt  Took or threatened to take negative or legal a...   

                                           Sub-issue  \
0                Information belongs to someone else   
1                   Denied request to lower payments   
2                           Account status incorrect   
3  Was not notified of investigation status or re...   
4  Threatened or suggested your credit would be d...   

                        Consumer complaint narrative  \
0                                                NaN   
1  I contacted Ally on Friday XX/XX/XXXX after fa...   
2                                                NaN   
3                                                NaN   
4                                                NaN   

                             Company public response  \
0                                                NaN   
1  Company has responded to the consumer and the ...   
2  Company has responded to the consumer and the ...   
3                                                NaN   
4                                                NaN   

                                  Company State ZIP code Tags  \
0       CAPITAL ONE FINANCIAL CORPORATION    PA    186XX  NaN   
1                     ALLY FINANCIAL INC.    NJ    088XX  NaN   
2  TRANSUNION INTERMEDIATE HOLDINGS, INC.    PA    19067  NaN   
3  TRANSUNION INTERMEDIATE HOLDINGS, INC.    GA    31707  NaN   
4              Medical Data Systems, Inc.    VA    22033  NaN   

  Consumer consent provided? Submitted via Date sent to company  \
0       Consent not provided           Web           2019-06-13   
1           Consent provided           Web           2019-11-01   
2       Consent not provided           Web           2019-04-01   
3                        NaN           Web           2021-11-01   
4                        NaN           Web           2021-11-02   

  Company response to consumer Timely response? Consumer disputed?  \
0      Closed with explanation              Yes                NaN   
1      Closed with explanation              Yes                NaN   
2      Closed with explanation              Yes                NaN   
3                  In progress              Yes                NaN   
4                  In progress              Yes                NaN   

   Complaint ID  
0       3274605  
1       3425257  
2       3198225  
3       4863965  
4       4866449

## Drop rows where the text column is empty

In [25]:
data.dropna(subset = [text_col_name],inplace=True)

In [26]:
data.head()

Date received                                            Product  \
1     2019-11-01                              Vehicle loan or lease   
7     2019-07-08  Credit reporting, credit repair services, or o...   
8     2020-06-10  Credit reporting, credit repair services, or o...   
10    2019-07-03  Credit reporting, credit repair services, or o...   
13    2019-03-21  Credit reporting, credit repair services, or o...   

                       Sub-product  \
1                             Loan   
7                 Credit reporting   
8                 Credit reporting   
10                Credit reporting   
13  Other personal consumer report   

                                                Issue  \
1                         Struggling to pay your loan   
7   Problem with a credit reporting company's inve...   
8                         Improper use of your report   
10               Incorrect information on your report   
13  Identity theft protection or other monitoring ...   

                                            Sub-issue  \
1                    Denied request to lower payments   
7   Their investigation did not fix an error on yo...   
8   Credit inquiries on your report that you don't...   
10                      Account information incorrect   
13         Received unwanted marketing or advertising   

                         Consumer complaint narrative  \
1   I contacted Ally on Friday XX/XX/XXXX after fa...   
7   Hello This complaint is against the three cred...   
8   I am a victim of Identity Theft & currently ha...   
10  Two accounts are still on my credit history af...   
13  Receiving daily telephone call ( s ) from XXXX...   

                              Company public response  \
1   Company has responded to the consumer and the ...   
7   Company has responded to the consumer and the ...   
8   Company has responded to the consumer and the ...   
10  Company has responded to the consumer and the ...   
13  Company has responded to the consumer and the ...   

                                   Company State ZIP code           Tags  \
1                      ALLY FINANCIAL INC.    NJ    088XX            NaN   
7   TRANSUNION INTERMEDIATE HOLDINGS, INC.    NY    109XX            NaN   
8      Experian Information Solutions Inc.    MT      NaN  Servicemember   
10     Experian Information Solutions Inc.    FL    328XX            NaN   
13                          NRA Group, LLC    MA      NaN            NaN   

   Consumer consent provided? Submitted via Date sent to company  \
1            Consent provided           Web           2019-11-01   
7            Consent provided           Web           2019-07-08   
8            Consent provided           Web           2020-06-10   
10           Consent provided           Web           2019-07-03   
13           Consent provided           Web           2019-03-27   

       Company response to consumer Timely response? Consumer disputed?  \
1           Closed with explanation              Yes                NaN   
7           Closed with explanation              Yes                NaN   
8           Closed with explanation              Yes                NaN   
10  Closed with non-monetary relief              Yes                NaN   
13          Closed with explanation              Yes                NaN   

    Complaint ID  
1        3425257  
7        3299394  
8        3692762  
10       3294745  
13       3186954

## Replace Duplicate labels

In [27]:
data.replace({label_col: product_map},inplace=True)

In [28]:
data.head()

Date received        Product                     Sub-product  \
1     2019-11-01   vehicle_loan                            Loan   
7     2019-07-08  credit_report                Credit reporting   
8     2020-06-10  credit_report                Credit reporting   
10    2019-07-03  credit_report                Credit reporting   
13    2019-03-21  credit_report  Other personal consumer report   

                                                Issue  \
1                         Struggling to pay your loan   
7   Problem with a credit reporting company's inve...   
8                         Improper use of your report   
10               Incorrect information on your report   
13  Identity theft protection or other monitoring ...   

                                            Sub-issue  \
1                    Denied request to lower payments   
7   Their investigation did not fix an error on yo...   
8   Credit inquiries on your report that you don't...   
10                      Account information incorrect   
13         Received unwanted marketing or advertising   

                         Consumer complaint narrative  \
1   I contacted Ally on Friday XX/XX/XXXX after fa...   
7   Hello This complaint is against the three cred...   
8   I am a victim of Identity Theft & currently ha...   
10  Two accounts are still on my credit history af...   
13  Receiving daily telephone call ( s ) from XXXX...   

                              Company public response  \
1   Company has responded to the consumer and the ...   
7   Company has responded to the consumer and the ...   
8   Company has responded to the consumer and the ...   
10  Company has responded to the consumer and the ...   
13  Company has responded to the consumer and the ...   

                                   Company State ZIP code           Tags  \
1                      ALLY FINANCIAL INC.    NJ    088XX            NaN   
7   TRANSUNION INTERMEDIATE HOLDINGS, INC.    NY    109XX            NaN   
8      Experian Information Solutions Inc.    MT      NaN  Servicemember   
10     Experian Information Solutions Inc.    FL    328XX            NaN   
13                          NRA Group, LLC    MA      NaN            NaN   

   Consumer consent provided? Submitted via Date sent to company  \
1            Consent provided           Web           2019-11-01   
7            Consent provided           Web           2019-07-08   
8            Consent provided           Web           2020-06-10   
10           Consent provided           Web           2019-07-03   
13           Consent provided           Web           2019-03-27   

       Company response to consumer Timely response? Consumer disputed?  \
1           Closed with explanation              Yes                NaN   
7           Closed with explanation              Yes                NaN   
8           Closed with explanation              Yes                NaN   
10  Closed with non-monetary relief              Yes                NaN   
13          Closed with explanation              Yes                NaN   

    Complaint ID  
1        3425257  
7        3299394  
8        3692762  
10       3294745  
13       3186954

## Encode the label column and save the encoder and encoded labels 

In [29]:
label_encoder = LabelEncoder()
label_encoder.fit(data[label_col])
labels = label_encoder.transform(data[label_col])

In [30]:
labels[0]

8

In [31]:
label_encoder.classes_

array(['card', 'credit_report', 'debt_collection', 'loan',
       'money_transfer', 'mortgage', 'others', 'savings_account',
       'vehicle_loan'], dtype=object)

In [32]:
data[label_col]

1             vehicle_loan
7            credit_report
8            credit_report
10           credit_report
13           credit_report
                ...       
2326240               card
2326241    debt_collection
2326242           mortgage
2326243      credit_report
2326244      credit_report
Name: Product, Length: 809343, dtype: object

In [33]:
label_path = r"C:\Users\Anonymous\OneDrive\RNN AND LSTM\output\labels.pkl"
label_encoder_path =  r"C:\Users\Anonymous\OneDrive\RNN AND LSTM\output\label_encoder.pkl"

In [34]:
save_file(label_path,labels)
save_file(label_encoder_path,label_encoder)

## Process text Column

In [35]:
input_text = data[text_col_name]

In [36]:
input_text = [i.lower() for i in tqdm(input_text)]

100%|██████████████████████████████████████████████████████████████████████| 809343/809343 [00:05<00:00, 155851.37it/s]


## Remove Punctuation except apostrophe

In [37]:
input_text = [re.sub(r"[^\w\d'\s]+"," ",i) for i in tqdm(input_text)]

100%|███████████████████████████████████████████████████████████████████████| 809343/809343 [01:06<00:00, 12133.49it/s]


In [38]:
input_text

['i contacted ally on friday xx xx xxxx after falling behind on payments due to being out of work for a short period of time due to an illness  i chated with a representative after logging into my account regarding my opitions to ensure i protect my credit and bring my account current  \n\nshe advised me that before an extenstion could be done  i had to make a payment in the amount of  270 00  i reviewed my finances  as i am playing catch up on all my bills and made this payment on monday xx xx xxxx  this rep advised me  once this payment posts to my account to contact ally back for an extention or to have a payment deffered to the end of my loan  \n\nwith this in mind  i contacted ally again today and chatted with xxxx  i explained all of the above and the information i was provided when i chatted with the rep last week  she asked several questions and advised me that a one or two month  extension deffered payment could be done however partial payment is needed  what  she advised me  

## Remove Digits

In [39]:
input_text = [re.sub("\d+","",i) for i in tqdm(input_text)]

100%|███████████████████████████████████████████████████████████████████████| 809343/809343 [00:39<00:00, 20622.35it/s]


In [40]:
input_text

['i contacted ally on friday xx xx xxxx after falling behind on payments due to being out of work for a short period of time due to an illness  i chated with a representative after logging into my account regarding my opitions to ensure i protect my credit and bring my account current  \n\nshe advised me that before an extenstion could be done  i had to make a payment in the amount of     i reviewed my finances  as i am playing catch up on all my bills and made this payment on monday xx xx xxxx  this rep advised me  once this payment posts to my account to contact ally back for an extention or to have a payment deffered to the end of my loan  \n\nwith this in mind  i contacted ally again today and chatted with xxxx  i explained all of the above and the information i was provided when i chatted with the rep last week  she asked several questions and advised me that a one or two month  extension deffered payment could be done however partial payment is needed  what  she advised me     or

## Remove more then one consecutive instance of 'x'

In [41]:
input_text = [re.sub(r'[x]{2,}',"",i) for i in tqdm(input_text)]

100%|███████████████████████████████████████████████████████████████████████| 809343/809343 [00:29<00:00, 27817.50it/s]


In [42]:
input_text

['i contacted ally on friday    after falling behind on payments due to being out of work for a short period of time due to an illness  i chated with a representative after logging into my account regarding my opitions to ensure i protect my credit and bring my account current  \n\nshe advised me that before an extenstion could be done  i had to make a payment in the amount of     i reviewed my finances  as i am playing catch up on all my bills and made this payment on monday     this rep advised me  once this payment posts to my account to contact ally back for an extention or to have a payment deffered to the end of my loan  \n\nwith this in mind  i contacted ally again today and chatted with   i explained all of the above and the information i was provided when i chatted with the rep last week  she asked several questions and advised me that a one or two month  extension deffered payment could be done however partial payment is needed  what  she advised me     or there abouts would 

## Replace multiple spaces with single space

In [43]:
input_text = [re.sub(' +'," ",i) for i in tqdm(input_text)]

100%|████████████████████████████████████████████████████████████████████████| 809343/809343 [01:32<00:00, 8746.15it/s]


In [44]:
input_text

['i contacted ally on friday after falling behind on payments due to being out of work for a short period of time due to an illness i chated with a representative after logging into my account regarding my opitions to ensure i protect my credit and bring my account current \n\nshe advised me that before an extenstion could be done i had to make a payment in the amount of i reviewed my finances as i am playing catch up on all my bills and made this payment on monday this rep advised me once this payment posts to my account to contact ally back for an extention or to have a payment deffered to the end of my loan \n\nwith this in mind i contacted ally again today and chatted with i explained all of the above and the information i was provided when i chatted with the rep last week she asked several questions and advised me that a one or two month extension deffered payment could be done however partial payment is needed what she advised me or there abouts would be due within days from me a

## Tokenize the text

In [45]:
tokens = [word_tokenize(t) for t in tqdm(input_text)]

100%|█████████████████████████████████████████████████████████████████████████| 809343/809343 [49:32<00:00, 272.31it/s]


In [46]:
tokens = [i[:20] if len(i) > 19 else ['<pad>'] * (20 - len(i)) + i for i in tqdm(tokens)]

100%|█████████████████████████████████████████████████████████████████████████| 809343/809343 [19:56<00:00, 676.26it/s]


## Convert tokens to integer indices from vocabulary

In [47]:
def token_index(tokens,vocabulary,missing = '<unk>'):
    idx_token = []
    for text in tqdm(tokens):
        idx_text = []
        for token in text:
            if token in vocabulary:
                idx_text.append(vocabulary.index(token))
            else:
                idx_text.append(vocabulary.index(missing))
        idx_token.append(idx_text)
    return idx_token

In [48]:
tokens = token_index(tokens,vocabulary)

100%|████████████████████████████████████████████████████████████████████████| 809343/809343 [4:10:01<00:00, 53.95it/s]


In [49]:
len(tokens)

809343

In [50]:
tokens[0]

[43,
 5909,
 3660,
 15,
 187,
 51,
 2333,
 563,
 15,
 3115,
 447,
 6,
 136,
 68,
 5,
 163,
 12,
 9,
 638,
 568]

In [51]:
data.head()

Date received        Product                     Sub-product  \
1     2019-11-01   vehicle_loan                            Loan   
7     2019-07-08  credit_report                Credit reporting   
8     2020-06-10  credit_report                Credit reporting   
10    2019-07-03  credit_report                Credit reporting   
13    2019-03-21  credit_report  Other personal consumer report   

                                                Issue  \
1                         Struggling to pay your loan   
7   Problem with a credit reporting company's inve...   
8                         Improper use of your report   
10               Incorrect information on your report   
13  Identity theft protection or other monitoring ...   

                                            Sub-issue  \
1                    Denied request to lower payments   
7   Their investigation did not fix an error on yo...   
8   Credit inquiries on your report that you don't...   
10                      Account information incorrect   
13         Received unwanted marketing or advertising   

                         Consumer complaint narrative  \
1   I contacted Ally on Friday XX/XX/XXXX after fa...   
7   Hello This complaint is against the three cred...   
8   I am a victim of Identity Theft & currently ha...   
10  Two accounts are still on my credit history af...   
13  Receiving daily telephone call ( s ) from XXXX...   

                              Company public response  \
1   Company has responded to the consumer and the ...   
7   Company has responded to the consumer and the ...   
8   Company has responded to the consumer and the ...   
10  Company has responded to the consumer and the ...   
13  Company has responded to the consumer and the ...   

                                   Company State ZIP code           Tags  \
1                      ALLY FINANCIAL INC.    NJ    088XX            NaN   
7   TRANSUNION INTERMEDIATE HOLDINGS, INC.    NY    109XX            NaN   
8      Experian Information Solutions Inc.    MT      NaN  Servicemember   
10     Experian Information Solutions Inc.    FL    328XX            NaN   
13                          NRA Group, LLC    MA      NaN            NaN   

   Consumer consent provided? Submitted via Date sent to company  \
1            Consent provided           Web           2019-11-01   
7            Consent provided           Web           2019-07-08   
8            Consent provided           Web           2020-06-10   
10           Consent provided           Web           2019-07-03   
13           Consent provided           Web           2019-03-27   

       Company response to consumer Timely response? Consumer disputed?  \
1           Closed with explanation              Yes                NaN   
7           Closed with explanation              Yes                NaN   
8           Closed with explanation              Yes                NaN   
10  Closed with non-monetary relief              Yes                NaN   
13          Closed with explanation              Yes                NaN   

    Complaint ID  
1        3425257  
7        3299394  
8        3692762  
10       3294745  
13       3186954

In [52]:
vocabulary[tokens[0][0]]

'i'

## Save the tokens

In [53]:
token_path = r"C:\Users\Anonymous\OneDrive\RNN AND LSTM\output\tokens.pkl"

In [54]:
save_file(token_path,tokens)

## Create Pytorch Dataset

In [80]:
class TextDataset(torch.utils.data.Dataset):

    def __init__(self, tokens, embeddings, labels):
        """
        :param tokens: List of word tokens
        :param embeddings: Word embeddings (from glove)
        :param labels: List of labels
        """
        self.tokens = tokens
        self.embeddings = embeddings
        self.labels = labels

    def __len__(self):
        return len(self.tokens)

    def __getitem__(self, idx):
        return self.labels[idx], self.embeddings[self.tokens[idx], :]

# Create Models

## RNN Model

In [81]:
class RNNNetwork(torch.nn.Module):

    def __init__(self, input_size, hidden_size, num_classes):
        """
        :param input_size: Size of embedding
        :param hidden_size: Hidden vector size
        :param num_classes: Number of classes in the dataset
        """
        super(RNNNetwork, self).__init__()
        # RNN Layer
        self.rnn = torch.nn.RNN(input_size=input_size,
                                hidden_size=hidden_size,
                                batch_first=True)
        # Linear Layer
        self.linear = torch.nn.Linear(hidden_size, num_classes)

    def forward(self, input_data):
        _, hidden = self.rnn(input_data)
        output = self.linear(hidden)
        return output

In [82]:
class LSTMNetwork(torch.nn.Module):

    def __init__(self, input_size, hidden_size, num_classes):
        """
        :param input_size: Size of embedding
        :param hidden_size: Hidden vector size
        :param num_classes: Number of classes in the dataset
        """
        super(LSTMNetwork, self).__init__()
        # LSTM Layer
        self.rnn = torch.nn.LSTM(input_size=input_size,
                                 hidden_size=hidden_size,
                                 batch_first=True)
        # Linear Layer
        self.linear = torch.nn.Linear(hidden_size, num_classes)

    def forward(self, input_data):
        _, (hidden, _) = self.rnn(input_data)
        output = self.linear(hidden[-1])
        return output

# Define Train function

In [61]:
def train(train_loader,valid_loader,model,criterion,optimizer,device,num_epochs,model_path):
    
    
    """
    Function to train the model
    :param train_loader: Data loader for train dataset
    :param valid_loader: Data loader for validation dataset
    :param model: Model object
    :param criterion: Loss function
    :param optimizer: Optimizer
    :param device: CUDA or CPU
    :param num_epochs: Number of epochs
    :param model_path: Path to save the model
    """
    best_loss = 1e8
    for i in range(num_epochs):
        print(f"Epoch {i+1} of {num_epochs}")
        valid_loss,train_loss = [],[]
        model.train()
        #train loop
        for batch_labels,batch_data in tqdm(train_loader):
            #move data to gpu if available 
            batch_labels = batch_labels.to(device)
            batch_labels = batch_labels.type(torch.LongTensor)
            batch_data = batch_data.to(device)
            #forward pass
            batch_output = model(batch_data)
            batch_output = torch.squeeze(batch_output)
            #calculate Loss
            loss = criterion(batch_output,batch_labels)
            train_loss.append(loss.item())
            optimizer.zero_grad()
            # backwards pass
            loss.backward()
            # Gradient update step
            optimizer.step()
        model.eval()
        # Validation loop
        for batch_labels,batch_data in tqdm(valid_loader):
            # Move data to gpu if available
            batch_labels = batch_labels.to(device)
            batch_labels = batch_labels.type(torch.LongTensor)
            batch_data = batch_data.to(device)
            # Forward pass
            batch_output = model(batch_data)
            batch_output = torch.squeeze(batch_output)
            # Calculate loss
            loss = criterion(batch_output, batch_labels)
            valid_loss.append(loss.item())
        t_loss = np.mean(train_loss)
        v_loss = np.mean(valid_loss)
        print(f"Train Loss : {t_loss}, Validation Loss: {v_loss}")
        if v_loss < best_loss:
            best_loss = v_loss
            # save model if validation loss improves
            torch.save(model.state_dict(),model_path)
        print(f"Best Validation Loss: {best_loss}")

# Define test  function

In [63]:
def test(test_loader,model,criterion,device):
    """
    Function to test the model
    param test_loader: Data loader for test dataset
    param model: Model object
    param criterion: Loss function
    param device: CUDA or CPU
    """
    model.eval()
    test_loss = []
    test_accu = []
    for batch_labels, batch_data in tqdm(test_loader):
        # Move data to device 
        batch_labels = batch_labels.to(device)
        batch_labels = batch_labels.type(torch.LongTensor)
        batch_data = batch_data.to(device)
        
        # Forward Pass
        batch_output = model(batch_data)
        batch_output = torch.squeeze(batch_output)
        # Calculate loss
        loss= criterion(batch_output, batch_labels)
        test_loss.append(loss.item())
        batch_preds = torch.agrmax(batch_output,axis =1 )
        # Move Prediciton to cpu
        if torch.cuda.is_available():
            batch_lables = batch_labels.cpu()
            batch_preds = batch_preds.cpu()
        # Compute accuracy
        test_accu.append(accuracy_score(batch_labels.detach().numpy(),batch_preds.detach().numpy()))
    test_loss = np.mean(test_loss)
    test_accu = np.mean(test_accu)
    print(f"Test Loss: {test_loss}, Test Accuracy: {test_accu}")

# Train RNN Model

## Load the files

In [67]:
tokens = load_file(token_path)
labels = load_file(label_path)
embeddings = load_file(embeddings_path)
label_encoder = load_file(label_encoder_path)
num_classes = len(label_encoder.classes_)

## Split data into train, Validation and test sets

In [83]:
x_train,x_test, y_train, y_test = train_test_split(tokens,labels, test_size=0.2)
x_train,x_valid,y_train,y_valid = train_test_split(x_train,y_train,test_size = 0.25)

## Create PyTorch Datasets

In [84]:
train_dataset = TextDataset(x_train,embeddings,y_train)
valid_dataset = TextDataset(x_valid,embeddings,y_valid)
test_dataset = TextDataset(x_test,embeddings,y_test)

## Create data loaders

In [85]:
train_loader = torch.utils.data.DataLoader(train_dataset, batch_size = 16, shuffle = True, drop_last = True)
valid_loader = torch.utils.data.DataLoader(valid_dataset,batch_size = 16)
test_loader = torch.utils.data.DataLoader(test_dataset,batch_size=16)

# Create Model Object 

In [86]:
model = RNNNetwork(input_size,hidden_size,num_classes)

## Move the model to Gpu if available

In [87]:
if torch.cuda.is_available():
    model = model.cuda()

## Define Loss Function and Optimizer

In [88]:
criterion = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(),lr=lr)
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [90]:
rnn_model_path =  r"C:\Users\Anonymous\OneDrive\RNN AND LSTM\output\model_rnn.pth"
lstm_model_path =  r"C:\Users\Anonymous\OneDrive\RNN AND LSTM\output\model_lstm.pth"

## Training Loop

In [91]:
train(train_loader,valid_loader,model,criterion,optimizer,device,num_epochs,rnn_model_path)

Epoch 1 of 100


100%|███████████████████████████████████████████████████████████████████████████| 10117/10117 [00:38<00:00, 262.89it/s]


Train Loss : 1.3270192542529773, Validation Loss: 1.1899582470572134
Best Validation Loss: 1.1899582470572134
Epoch 2 of 100


100%|███████████████████████████████████████████████████████████████████████████| 10117/10117 [00:37<00:00, 270.51it/s]


Train Loss : 1.103426886889255, Validation Loss: 1.0865435742237262
Best Validation Loss: 1.0865435742237262
Epoch 3 of 100


...

Train Loss : 0.7542295694577046, Validation Loss: 0.784620647478377
Best Validation Loss: 0.7717261959058418
Epoch 99 of 100


100%|███████████████████████████████████████████████████████████████████████████| 10117/10117 [00:58<00:00, 172.39it/s]


Train Loss : 0.7537687969583361, Validation Loss: 0.7709106346935674
Best Validation Loss: 0.7709106346935674
Epoch 100 of 100


100%|███████████████████████████████████████████████████████████████████████████| 10117/10117 [00:36<00:00, 275.47it/s]


Train Loss : 0.7537694163730941, Validation Loss: 0.7974834278059463
Best Validation Loss: 0.7709106346935674


## Train LSTM

In [92]:
model = LSTMNetwork(input_size,hidden_size,num_classes)

In [93]:
if torch.cuda.is_available():
    model = model.cuda()

In [94]:
criterion = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(),lr=lr)
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [95]:
train(train_loader,valid_loader,model,criterion,optimizer,device,num_epochs,lstm_model_path)

Epoch 1 of 100


100%|███████████████████████████████████████████████████████████████████████████| 10117/10117 [00:34<00:00, 291.24it/s]


Train Loss : 1.0717882515359947, Validation Loss: 0.8975599931494643
Best Validation Loss: 0.8975599931494643
Epoch 2 of 100


100%|███████████████████████████████████████████████████████████████████████████| 10117/10117 [00:34<00:00, 290.35it/s]


Train Loss : 0.857142892966946, Validation Loss: 0.828357910755254
Best Validation Loss: 0.828357910755254
Epoch 3 of 100


...

Train Loss : 0.6185685955793205, Validation Loss: 0.6832681337729195
Best Validation Loss: 0.6798167092832603
Epoch 99 of 100


100%|███████████████████████████████████████████████████████████████████████████| 10117/10117 [00:28<00:00, 357.35it/s]


Train Loss : 0.6182946378710684, Validation Loss: 0.6845364154233543
Best Validation Loss: 0.6798167092832603
Epoch 100 of 100


100%|███████████████████████████████████████████████████████████████████████████| 10117/10117 [00:46<00:00, 217.93it/s]

Train Loss : 0.6180214131380473, Validation Loss: 0.6823255994847915
Best Validation Loss: 0.6798167092832603


## Predict on new text

In [96]:
input_text = '''I am a victim of Identity Theft & currently have an Experian account that 
I can view my Experian Credit Report and getting notified when there is activity on 
my Experian Credit Report. For the past 3 days I've spent a total of approximately 9 
hours on the phone with Experian. Every time I call I get transferred repeatedly and 
then my last transfer and automated message states to press 1 and leave a message and 
someone would call me. Every time I press 1 I get an automatic message stating than you 
before I even leave a message and get disconnected. I call Experian again, explain what 
is happening and the process begins again with the same end result. I was trying to have 
this issue attended and resolved informally but I give up after 9 hours. There are hard 
hit inquiries on my Experian Credit Report that are fraud, I didn't authorize, or recall 
and I respectfully request that Experian remove the hard hit inquiries immediately just 
like they've done in the past when I was able to speak to a live Experian representative 
in the United States. The following are the hard hit inquiries : BK OF XXXX XX/XX/XXXX 
XXXX XXXX XXXX  XX/XX/XXXX XXXX  XXXX XXXX  XX/XX/XXXX XXXX  XX/XX/XXXX XXXX  XXXX 
XX/XX/XXXX'''

## process input text

In [97]:
input_text = input_text.lower()
input_text = re.sub(r"[^\w\d'\s]+", " ", input_text)
input_text = re.sub("\d+", "", input_text)
input_text = re.sub(r'[x]{2,}', "", input_text)
input_text = re.sub(' +', ' ', input_text)
tokens = word_tokenize(input_text)

## Add padding if the length of token is less than 20 

In [98]:
tokens = ['<pad>']*(20-len(tokens))+tokens

## Tokenize the input text

In [99]:
idx_token = []
for token in tokens:
    if token in vocabulary:
        idx_token.append(vocabulary.index(token))
    else:
        idx_token.append(vocabulary.index('<unk>'))
        

## Get Embeddings for tokens

In [100]:
token_emb = embeddings[idx_token,:]

## convert to torch tensor

In [101]:
inp = torch.from_numpy(token_emb)

## CReate a bacth of one record

In [102]:
inp = torch.unsqueeze(inp,0)

## Load label encoder

In [103]:
label_encoder = load_file(label_encoder_path)
num_classes = len(label_encoder.classes_)

# RNN prediction

In [104]:
# Create model object
model = RNNNetwork(input_size, hidden_size, num_classes)

# Load trained weights
model.load_state_dict(torch.load(rnn_model_path))

# Move the model to GPU if available
if torch.cuda.is_available():
    model = model.cuda()
    
# Forward pass
out = torch.squeeze(model(inp))

# Find predicted class
prediction = label_encoder.classes_[torch.argmax(out)]
print(f"Predicted  Class: {prediction}")

Predicted  Class: credit_report


## LSTM Prediction

In [105]:
# Create model object
model = LSTMNetwork(input_size, hidden_size, num_classes)

# Load trained weights
model.load_state_dict(torch.load(lstm_model_path))

# Move the model to GPU if available
if torch.cuda.is_available():
    model = model.cuda()
    
# Forward pass
out = torch.squeeze(model(inp))

# Find predicted class
prediction = label_encoder.classes_[torch.argmax(out)]
print(f"Predicted  Class: {prediction}")

Predicted  Class: credit_report
